# Final Model

In [3]:
import pandas as pd
from gensim import models,corpora
import pyLDAvis.gensim
from gensim.models.coherencemodel import CoherenceModel
import warnings

In [4]:
pd.set_option('max_colwidth',400)
pyLDAvis.enable_notebook()
warnings.filterwarnings('ignore')

In [5]:
Lda = models.LdaMulticore
lda_final =Lda.load('lda_final')
dictionary = corpora.Dictionary.load('dictionary')
doc_term_matrix = corpora.MmCorpus('doc_term_matrix.mm')

One stupid thing with LDA in gensim is when it shows the top coherent topics, it shows the word representation and the coherence score but it doesnt map with the topic id. The next cell is to overcome that issue and correctly map coherence score with the right topic id

# Topic Evaluation 

In [70]:
a = lda_final.show_topics(num_topics=12,formatted=False,num_words=10)
b = lda_final.top_topics(doc_term_matrix,dictionary=dictionary,topn=10) # This orders the topics in the decreasing order of coherence score

topic2skillb = {}
topic2csb = {}
topic2skilla = {}
topic2csa = {}
num_topics =lda_final.num_topics
cnt =1

for ws in b:
    wset = set(w[1] for w in ws[0])
    topic2skillb[cnt] = wset
    topic2csb[cnt] = ws[1]
    cnt +=1

for ws in a:
    wset = set(w[0]for w in ws[1])
    topic2skilla[ws[0]+1] = wset
    
for i in range(1,num_topics+1):
    for j in range(1,num_topics+1):  
        if topic2skilla[i].intersection(topic2skillb[j])==topic2skilla[i]:
            topic2csa[i] = topic2csb[j]

finalData = pd.DataFrame([],columns=['Topic','words'])
finalData['Topic']=topic2skilla.keys()
finalData['Topic'] = finalData['Topic'].apply(lambda x: 'Topic'+str(x))
finalData['words']=topic2skilla.values()
finalData['cs'] = topic2csa.values()
finalData.sort_values(by='cs',ascending=False,inplace=True)
finalData.to_csv('CoherenceScore.csv')
finalData

Topic  \
8    Topic9   
9   Topic10   
11  Topic12   
6    Topic7   
1    Topic2   
0    Topic1   
4    Topic5   
5    Topic6   
2    Topic3   
3    Topic4   
10  Topic11   
7    Topic8   

                                                                                            words  \
8                            {spark, python, r, tableau, technical, hive, pig, java, hadoop, sql}   
9                                  {python, css, mysql, c, html, java, javascript, sql, c++, php}   
11                            {sas, python, r, excel, tableau, technical, matlab, java, sql, c++}   
6                      {spark, hadoop, python, r, tableau, technical, pandas, scikit, sql, numpy}   
1                                 {ms, python, r, technical, c, data, java, sql, oracle, windows}   
0                              {xml, technical, html, java, uml, sql, pl, windows, oracle, agile}   
4                     {skills, computer, python, r, excel, technical, matlab, data, sql, windows}   
5                    {means, key, excel, technical, k, access, teradata, sql, sql_server, oracle}   
2                     {project, core, computer, analytics, analysis, r, team, data, areasof, c++}   
3    {project, skills, linkedin, powershell, salesforce, unix, technical, bullhorn, linux, taleo}   
10  {relevant, research, illustrator, french, data, spanish, native, english, mandarin, indesign}   
7                                     {s., d., core, software, m., skill, jobvite, j., r., taleo}   

           cs  
8   -0.937897  
9   -1.086996  
11  -1.159532  
6   -1.333507  
1   -1.502323  
0   -1.657700  
4   -1.827899  
5   -2.382989  
2   -2.893935  
3   -6.654834  
10 -10.106876  
7  -11.682204

# Visualizing with pyLDAviz

In [66]:
num_topics =12
vis = pyLDAvis.gensim.prepare(lda_final, doc_term_matrix, dictionary,sort_topics=False)
pyLDAvis.save_html(vis,f'pyLDAvis_{num_topics}.html')
vis

PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
0       7.238229        1       1 -0.028248 -0.179300
1       3.746417        1       2  0.012753 -0.027564
2       2.335267        1       3  0.122807  0.011622
3       2.674761        1       4  0.151100 -0.037611
4       3.370106        1       5  0.074784  0.057546
5       2.191426        1       6  0.132711  0.022145
6      20.330587        1       7 -0.204531  0.141215
7       3.048626        1       8  0.158089  0.021893
8      17.504662        1       9 -0.230710 -0.043406
9      14.389081        1      10 -0.171886 -0.107890
10      2.149308        1      11  0.161517  0.042300
11     21.021530        1      12 -0.178386  0.099050, topic_info=     Category         Freq          Term        Total  loglift  logprob
term                                                                   
81    Default  1530.000000           sas  1530.000000  30.0000  30.0000
99    Default   701.000000        pandas   701.000000  29.0000  29.0000
21    Default  1020.000000    javascript  1020.000000  28.0000  28.0000
75    Default  1058.000000          hive  1058.000000  27.0000  27.0000
2     Default  1114.000000          html  1114.000000  26.0000  26.0000
0     Default   656.000000           css   656.000000  25.0000  25.0000
150   Default   567.000000         numpy   567.000000  24.0000  24.0000
100   Default   458.000000        scikit   458.000000  23.0000  23.0000
204   Default   646.000000           pig   646.000000  22.0000  22.0000
7     Default  3289.000000             r  3289.000000  21.0000  21.0000
6     Default  3500.000000        python  3500.000000  20.0000  20.0000
27    Default  1092.000000         excel  1092.000000  19.0000  19.0000
31    Default  1462.000000        matlab  1462.000000  18.0000  18.0000
20    Default  1851.000000          java  1851.000000  17.0000  17.0000
139   Default   395.000000           php   395.000000  16.0000  16.0000
39    Default   357.000000         hbase   357.000000  15.0000  15.0000
252   Default   300.000000    matplotlib   300.000000  14.0000  14.0000
82    Default   954.000000         spark   954.000000  13.0000  13.0000
47    Default   515.000000    powerpoint   515.000000  12.0000  12.0000
898   Default   286.000000         sqoop   286.000000  11.0000  11.0000
13    Default  1582.000000             c  1582.000000  10.0000  10.0000
259   Default   359.000000         scipy   359.000000   9.0000   9.0000
195   Default   684.000000          spss   684.000000   8.0000   8.0000
253   Default   302.000000         learn   302.000000   7.0000   7.0000
216   Default   513.000000           xml   513.000000   6.0000   6.0000
78    Default   337.000000    regression   337.000000   5.0000   5.0000
269   Default   257.000000        jquery   257.000000   4.0000   4.0000
38    Default  1346.000000        hadoop  1346.000000   3.0000   3.0000
93    Default   370.000000           svm   370.000000   2.0000   2.0000
107   Default   357.000000    clustering   357.000000   1.0000   1.0000
...       ...          ...           ...          ...      ...      ...
81    Topic12  1052.860840           sas  1530.139893   1.1858  -3.4139
106   Topic12   306.949036        access   418.801880   1.2489  -4.6465
59    Topic12   308.074188      computer   438.480194   1.2066  -4.6429
742   Topic12    43.209030         maple    53.736332   1.3416  -6.6072
567   Topic12    34.163467  spss_modeler    42.265919   1.3468  -6.8421
31    Topic12   850.477356        matlab  1462.463989   1.0175  -3.6274
170   Topic12   129.183517         latex   185.219879   1.1993  -5.5120
7     Topic12  1540.567017             r  3289.287109   0.8011  -3.0333
1445  Topic12    95.578224   mathematica   136.352020   1.2043  -5.8133
8     Topic12  1368.419189           sql  3209.395996   0.7072  -3.1518
6     Topic12  1386.641113        python  3500.394531   0.6336  -3.1386
10    Topic12   691.729248       

## How to pick relevant words in each topic?

In [25]:
token_percent = vis.topic_coordinates.sort_values(by='topics').loc[:,['topics','Freq']]

In [77]:
def get_relevant_words(vis,lam=0.3,topn=10):
    a = vis.topic_info
    a['finalscore'] = a['logprob']*lam+(1-lam)*a['loglift']
    a = a.loc[:,['Category','Term','finalscore']].groupby(['Category'])\
    .apply(lambda x: x.sort_values(by='finalscore',ascending=False).head(topn))
    a = a.loc[:,'Term'].reset_index().loc[:,['Category','Term']]
    a = a[a['Category']!='Default']
    a = a.to_dict('split')['data']
    d ={}
    for k,v in a: 
        if k not in d.keys():
            d[k] =set()
            d[k].add(v)
        else:
            d[k].add(v)
    finalData = pd.DataFrame([],columns=['Topic','words with Relevance'])
    finalData['Topic']=d.keys()
    finalData['words with Relevance']=d.values()
    return finalData

In [91]:
get_relevant_words(vis,0.3).merge(finalData,how='left',on ='Topic').sort_values(by='cs',ascending=False).iloc[:,[0,1]]

Topic  \
11   Topic9   
1   Topic10   
3   Topic12   
9    Topic7   
4    Topic2   
0    Topic1   
7    Topic5   
8    Topic6   
5    Topic3   
6    Topic4   
2   Topic11   
10   Topic8   

                                                                                                 words with Relevance  
11                                            {sqoop, kafka, cassandra, hdfs, hbase, hive, pig, impala, flume, oozie}  
1                                                 {jquery, xml, css, eclipse, html, c, ajax, django, javascript, php}  
3                                                 {sas, powerpoint, python, r, excel, matlab, spss, sql, word, stata}  
9                               {classification, svm, learn, k, scikit, pandas, regression, matplotlib, scipy, numpy}  
4   {mssuite2012, tmux, spark2.0, databaseand, tableau_8, hive2.8, windows7/8/10, hadoop2, electronic, python2.7/3.3}  
0                                                       {jboss, weblogic, ant, rmi, struts, soap, jsf, uml, jms, cvs}  
7                          {linearandnon, hplc, mexico, gc, community, volunteer, tika, excelandword, pune, ontology}  
8                {ggplot2and, gridsearchand, oncology, modeltuning/, ddl, stepwise, filter_methods, hiv, pigand, dml}  
5        {magento, public_health, copy, campaign, hebrew, lucid, oracle_rdbms, ubuntuand, spatialdata, linearalgebra}  
6                 {dataquality, erecruit, d.c., brassring, google_earth, october, scorecards, bullhorn, icims, taleo}  
2                     {french, spanish, native, testing/, hootsuite, english, chinese, mandarin, cantonese, indesign}  
10                                                                      {s., d., l., n., m., y., jobvite, g., j., p.}